In [70]:
import pandas as pd
import numpy as np
csvfile = '/home/amrita95/Desktop/HBA Project/EEG_data.csv'
samples = pd.read_csv(csvfile)


In [71]:
print(np.shape(samples))

(12811, 15)


In [72]:
print(samples.columns)
col = ['SubjectID','VideoID','user-definedlabeln']
features = samples.drop(col,axis=1)

Index(['SubjectID', 'VideoID', 'Attention', 'Mediation', 'Raw', 'Delta',
       'Theta', 'Alpha1', 'Alpha2', 'Beta1', 'Beta2', 'Gamma1', 'Gamma2',
       'predefinedlabel', 'user-definedlabeln'],
      dtype='object')


In [73]:
print(features.head())

   Attention  Mediation    Raw      Delta     Theta    Alpha1   Alpha2  \
0       56.0       43.0  278.0   301963.0   90612.0   33735.0  23991.0   
1       40.0       35.0  -50.0    73787.0   28083.0    1439.0   2240.0   
2       47.0       48.0  101.0   758353.0  383745.0  201999.0  62107.0   
3       47.0       57.0   -5.0  2012240.0  129350.0   61236.0  17084.0   
4       44.0       53.0   -8.0  1005145.0  354328.0   37102.0  88881.0   

     Beta1     Beta2   Gamma1   Gamma2  predefinedlabel  
0  27946.0   45097.0  33228.0   8293.0              0.0  
1   2746.0    3687.0   5293.0   2740.0              0.0  
2  36293.0  130536.0  57243.0  25354.0              0.0  
3  11488.0   62462.0  49960.0  33932.0              0.0  
4  45307.0   99603.0  44790.0  29749.0              0.0  


In [74]:
print(np.shape(features))

(12811, 12)


In [75]:
a = samples.groupby(['SubjectID','VideoID'])[features.columns[0]].count()

In [87]:
df = pd.DataFrame(columns=samples.columns)
for i in range(10):
    for j in range(10):
        a = samples.loc[(samples['SubjectID']==i) & (samples['VideoID']==j)]
        df = df.append(a[0:112])

col = ['SubjectID','VideoID','predefinedlabel']
features = df.drop(col,axis=1)
aa = np.array(features)
print(np.shape(features))

print(features.groupby(['user-definedlabeln']).count())

(11200, 12)
                    Attention  Mediation   Raw  Delta  Theta  Alpha1  Alpha2  \
user-definedlabeln                                                             
0.0                      5488       5488  5488   5488   5488    5488    5488   
1.0                      5712       5712  5712   5712   5712    5712    5712   

                    Beta1  Beta2  Gamma1  Gamma2  
user-definedlabeln                                
0.0                  5488   5488    5488    5488  
1.0                  5712   5712    5712    5712  


In [77]:


X_input= aa[:,0:11]
Y_input= aa[:,11]

print(np.shape(X_input),np.shape(Y_input))





(11200, 11) (11200,)


In [95]:
from keras.models import Sequential
from keras.layers import LSTM, Dense,TimeDistributed, Bidirectional
from keras.layers import BatchNormalization
from sklearn.model_selection import KFold 

kfold = KFold(n_splits=10, shuffle=False,random_state=None)
cvscores = []



for train, test in kfold.split(X_input, Y_input):
    X_train,Y_train = X_input[train], Y_input[train]
    X_test, Y_test = X_input[test], Y_input[test]
    

    print(np.shape(X_train),np.shape(X_test))
    X_train= (np.reshape(np.array(X_train),(90,112,11)))
    Y_train= (np.reshape(np.array(Y_train),(90,112,1)))
    
    X_test= (np.reshape(X_test,(10,112,11)))
    Y_test= (np.reshape(Y_test,(10,112,1)))

    model = Sequential()
    
    model.add(BatchNormalization(input_shape=(112,11)))
    model.add((LSTM(50,input_shape=(112,11),activation='tanh',return_sequences=True)
                            ))
    model.add(TimeDistributed(Dense(1,activation='sigmoid')))
    
    model.compile(optimizer='Adam',loss='binary_crossentropy',metrics=['acc'])
    model.fit(X_train, Y_train, epochs=500, batch_size=10, verbose=1)
    scores = model.evaluate(X_test, Y_test, verbose=1)
    print("%s: %.2f%%" % (model.metrics_names[1], scores[1]*100))
    cvscores.append(scores[1] * 100)
    
print('%.2f%% (+/- %.2f%%)' % ((np.mean(cvscores)), np.std(cvscores)))

(10080, 11) (1120, 11)


Epoch 1/500


10/90 [==>...........................] - ETA: 9s - loss: 0.7469 - acc: 0.3991

30/90 [=========>....................] - ETA: 2s - loss: 0.7151 - acc: 0.4515

50/90 [===============>..............] - ETA: 1s - loss: 0.7095 - acc: 0.4530

...

40/90 [============>.................] - ETA: 0s - loss: 0.2525 - acc: 0.8920

50/90 [===============>..............] - ETA: 0s - loss: 0.2461 - acc: 0.8964

60/90 [===================>..........] - ETA: 0s - loss: 0.2767 - acc: 0.8824

70/90 [======================>.......] - ETA: 0s - loss: 0.2699 - acc: 0.8849

80/90 [=========================>....] - ETA: 0s - loss: 0.3042 - acc: 0.8699

In [11]:
model.fit(X_train, Y_train, epochs=500, batch_size=10, verbose=True,validation_data=(X_test,Y_test))

Train on 90 samples, validate on 10 samples
Epoch 1/500


10/90 [==>...........................] - ETA: 5s - loss: 0.6580 - acc: 0.6625

20/90 [=====>........................] - ETA: 2s - loss: 0.6891 - acc: 0.5866

30/90 [=========>....................] - ETA: 1s - loss: 0.6665 - acc: 0.6449

40/90 [============>.................] - ETA: 1s - loss: 0.6753 - acc: 0.6174

...

50/90 [===============>..............] - ETA: 0s - loss: 0.2736 - acc: 0.8729

60/90 [===================>..........] - ETA: 0s - loss: 0.2507 - acc: 0.8869

70/90 [======================>.......] - ETA: 0s - loss: 0.2631 - acc: 0.8782

80/90 [=========================>....] - ETA: 0s - loss: 0.2629 - acc: 0.8806

90/90 [==============================] - 1s 7ms/step - loss: 0.2867 - acc: 0.8624 - val_loss: 1.1372 - val_acc: 0.5045


In [ ]:
model.save_weights('/home/amrita95/Desktop/HBA Project/weights.h5')